In [134]:
import openpyxl
from openpyxl.styles import Alignment
import requests
from bs4 import BeautifulSoup
import json
import concurrent.futures
import os
import json
import pandas as pd
from requests.adapters import HTTPAdapter
from urllib3.util.retry import Retry
import time


In [135]:
cntyCds = {"CH","BD","CA","IN","KH","PH","SG","TH","AU","CL","TW","JP","CN","GB","EU","US"}

In [143]:
def get_link_list(cntyCds):
        # URL của API
    url = "https://unipass.customs.go.kr/clip/prlstclsfsrch/retrievePrlstClsfCaseLst.do"
        
        # Headers của yêu cầu
    headers = {
            'Accept': 'application/json, text/javascript, */*; q=0.01',
            'Accept-Language': 'en-US,en;q=0.9,vi-VN;q=0.8,vi;q=0.7,fr-FR;q=0.6,fr;q=0.5',
            'Connection': 'keep-alive',
            'Content-Type': 'application/x-www-form-urlencoded; charset=UTF-8',
            'Cookie': 'WMONID=PrQbL04HN94; JSESSIONID=0001QEkyah0hPybS5B8l72lu5sN66qPDua8EuJLATsU9U2O4a48A8opBefekkxF-oK6X35ZbCYaclUatspLmr_JtTHoTUlk6y_EdohZShZVj65_39JPhQ4_pBRGAXPEo0vry:eul11',
            'Origin': 'https://unipass.customs.go.kr',
            'Referer': 'https://unipass.customs.go.kr/clip/index.do',
            'Sec-Fetch-Dest': 'empty',
            'Sec-Fetch-Mode': 'cors',
            'Sec-Fetch-Site': 'same-origin',
            'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/128.0.0.0 Safari/537.36',
            'X-Requested-With': 'XMLHttpRequest',
            'isAjax': 'true',
            'sec-ch-ua': '"Chromium";v="128", "Not;A=Brand";v="24", "Google Chrome";v="128"',
            'sec-ch-ua-mobile': '?0',
            'sec-ch-ua-platform': '"macOS"'
        }

        # Tạo các danh sách để chứa kết quả
    reffNoNm_lists = []
        
        # Lặp qua các giá trị cntyCd

    for cntyCd in cntyCds:
        pageIndex = 1
        while True:
            # Dữ liệu body của yêu cầu
            data = {
                'pageIndex': pageIndex,
                'pageUnit': 1000,  # Số bản ghi trên mỗi trang
                'orderColumns': 'ENFR_DT desc',
                'cntyCd': cntyCd,
                'srchYn': 'Y',
                'scrnTp': 'WDTH',
                'lngaTp': 'org',
            }

            # Thực hiện yêu cầu POST
            response = requests.post(url, headers=headers, data=data).json()
            
            # Lấy tổng số trang từ phản hồi
            totalPageCount = response["paginationInfo"]["totalPageCount"]
            
            print(f"Đang tải {cntyCd}, trang {pageIndex}/{totalPageCount}. Số lượng: {response['uls_over']['count']}")
            
            # Dừng vòng lặp nếu đã vượt quá số trang
            if pageIndex > totalPageCount:
                break
            
            for item in response['uls_over']["itemList"]:
                item_info = {}
                item_info['cntyCd']= item['CNTY_CD']
                item_info['baseYy']= item['BASE_YY']
                item_info['reffNoNm']=item['REFF_NO_NM']
                item_info['prlstClsfSrno'] = item['PRLST_CLSF_SRNO']
                print(item_info)
                            
                reffNoNm_lists.append(item_info)
            # Tăng chỉ số trang để tiếp tục lặp
            pageIndex += 1
    df = pd.DataFrame(reffNoNm_lists)
    return df

In [ ]:
links_list = get_link_list(cntyCds)

Đang tải TW, trang 1/16. Số lượng: 1000
{'cntyCd': 'TW', 'baseYy': '2024', 'reffNoNm': '113BA0093', 'prlstClsfSrno': '4'}
{'cntyCd': 'TW', 'baseYy': '2024', 'reffNoNm': '113CA0132', 'prlstClsfSrno': '33'}
{'cntyCd': 'TW', 'baseYy': '2024', 'reffNoNm': '113BA0091', 'prlstClsfSrno': '21'}
{'cntyCd': 'TW', 'baseYy': '2024', 'reffNoNm': '113AA0287', 'prlstClsfSrno': '13'}
{'cntyCd': 'TW', 'baseYy': '2024', 'reffNoNm': '113CA0127', 'prlstClsfSrno': '41'}
{'cntyCd': 'TW', 'baseYy': '2024', 'reffNoNm': '113CA0128', 'prlstClsfSrno': '39'}
{'cntyCd': 'TW', 'baseYy': '2024', 'reffNoNm': '113CA0125', 'prlstClsfSrno': '24'}
{'cntyCd': 'TW', 'baseYy': '2024', 'reffNoNm': '113CA0126', 'prlstClsfSrno': '6'}
{'cntyCd': 'TW', 'baseYy': '2024', 'reffNoNm': '113CA0119', 'prlstClsfSrno': '38'}
{'cntyCd': 'TW', 'baseYy': '2024', 'reffNoNm': '113CA0121', 'prlstClsfSrno': '35'}
{'cntyCd': 'TW', 'baseYy': '2024', 'reffNoNm': '113AA0277', 'prlstClsfSrno': '18'}
{'cntyCd': 'TW', 'baseYy': '2024', 'reffNoNm': '1